In [5]:
import numpy as np
from scipy import stats
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import torch

from collections import Counter

import sklearn
from sklearn.preprocessing import LabelEncoder, MinMaxScaler

# from nas_201_api import NASBench201API as API
# from nas_201_api import ResultsCount
# from nas_201_api import ArchResults

In [7]:
df = pd.read_csv("/home/gean/nns_performance_prediction/meta_datasets/nasbench201_tabular.csv")
df 

Unnamed: 0  id_arch  \
0                0        0   
1                1        0   
2                2        0   
3                3        0   
4                4        0   
...            ...      ...   
281245      281245    15624   
281246      281246    15624   
281247      281247    15624   
281248      281248    15624   
281249      281249    15624   

                                                 str_arch  \
0       |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
1       |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
2       |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
3       |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
4       |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
...                                                   ...   
281245  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   
281246  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   
281247  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   
281248  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   
281249  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   

                                               layers_all  \
0       ['avg_pool_3x3', 'nor_conv_1x1', 'skip_connect...   
1       ['avg_pool_3x3', 'nor_conv_1x1', 'skip_connect...   
2       ['avg_pool_3x3', 'nor_conv_1x1', 'skip_connect...   
3       ['avg_pool_3x3', 'nor_conv_1x1', 'skip_connect...   
4       ['avg_pool_3x3', 'nor_conv_1x1', 'skip_connect...   
...                                                   ...   
281245  ['nor_conv_1x1', 'none', 'nor_conv_1x1', 'none...   
281246  ['nor_conv_1x1', 'none', 'nor_conv_1x1', 'none...   
281247  ['nor_conv_1x1', 'none', 'nor_conv_1x1', 'none...   
281248  ['nor_conv_1x1', 'none', 'nor_conv_1x1', 'none...   
281249  ['nor_conv_1x1', 'none', 'nor_conv_1x1', 'none...   

                                         adjacency_matrix         dataset  \
0       [[0. 0. 0. 0.]\n [4. 0. 0. 0.]\n [2. 1. 0. 0.]...   cifar10-valid   
1       [[0. 0. 0. 0.]\n [4. 0. 0. 0.]\n [2. 1. 0. 0.]...   cifar10-valid   
2       [[0. 0. 0. 0.]\n [4. 0. 0. 0.]\n [2. 1. 0. 0.]...   cifar10-valid   
3       [[0. 0. 0. 0.]\n [4. 0. 0. 0.]\n [2. 1. 0. 0.]...   cifar10-valid   
4       [[0. 0. 0. 0.]\n [4. 0. 0. 0.]\n [2. 1. 0. 0.]...   cifar10-valid   
...                                                   ...             ...   
281245  [[0. 0. 0. 0.]\n [2. 0. 0. 0.]\n [0. 2. 0. 0.]...  ImageNet16-120   
281246  [[0. 0. 0. 0.]\n [2. 0. 0. 0.]\n [0. 2. 0. 0.]...  ImageNet16-120   
281247  [[0. 0. 0. 0.]\n [2. 0. 0. 0.]\n [0. 2. 0. 0.]...  ImageNet16-120   
281248  [[0. 0. 0. 0.]\n [2. 0. 0. 0.]\n [0. 2. 0. 0.]...  ImageNet16-120   
281249  [[0. 0. 0. 0.]\n [2. 0. 0. 0.]\n [0. 2. 0. 0.]...  ImageNet16-120   

        epoch  conv_num_layers  conv_kernel_min  conv_kernel_max  ...  \
0           1                2                1                1  ...   
1           4                2                1                1  ...   
2          12                2                1                1  ...   
3          36                2                1                1  ...   
4         108                2                1                1  ...   
...       ...              ...              ...              ...  ...   
281245      4                4                1                1  ...   
281246     12                4                1                1  ...   
281247     36                4                1                1  ...   
281248    108                4                1                1  ...   
281249    200                4                1                1  ...   

         latency    time_train  time_valid  time_test  loss_train  loss_valid  \
0       0.013936      7.221093    2.548979        NaN    1.919065    1.806851   
1       0.013936     28.884372   10.195917        NaN    1.504583    1.919403   
2       0.013936     86.653116   30.587751        NaN    1.166258    1.733641   
3       0.013936    259.959348   91.763253 

In [10]:
df['params'].describe()

count    281250.000000
mean          0.402388
std           0.232200
min           0.073306
25%           0.164456
50%           0.351496
75%           0.587386
max           1.538696
Name: params, dtype: float64

In [21]:
def extract_layers(api, arch_str) -> list:
    """
    there are always 3 nodes, besides node 0
    1-dim = node, 2-dim = edge, 3-dim = layer (0) or edge origin (1)
    i.e:
    input: |avg_pool_3x3~0|+|nor_conv_1x1~0|none~1|+|nor_conv_3x3~0|skip_connect~1|skip_connect~2|
    output: ['avg_pool_3x3', 'nor_conv_1x1', 'none', 'nor_conv_3x3', 'skip_connect', 'skip_connect']
    """
    
    layers = []
    nodes = api.str2lists(arch_str)
    
    node_1 = nodes[0]
    layers.append(node_1[0][0])
    node_2 = nodes[1]
    layers.append(node_2[0][0])
    layers.append(node_2[1][0])
    node_3 = nodes[2]
    layers.append(node_3[0][0])
    layers.append(node_3[1][0])
    layers.append(node_3[2][0])
    
    return layers

In [22]:
def get_arch_stats(layers : list) -> dict:
    remaining_arch_stats = {'avg_pool_num_layers': 0, 'skip_connection_num_layers': 0, 'zeroize_num_layers': 0}
    conv_layers = []
    
    for layer in layers:
        if layer == 'nor_conv_1x1': conv_layers.append(1)
        elif layer == 'nor_conv_3x3': conv_layers.append(3)
        elif layer == 'avg_pool_3x3': remaining_arch_stats['avg_pool_num_layers'] += 1
        elif layer == 'skip_connect': remaining_arch_stats['skip_connection_num_layers'] += 1
        elif layer == 'none': remaining_arch_stats['zeroize_num_layers'] += 1
        else: raise ValueError('Invalid layer type')
    
    conv_stats = extract_conv_stats(conv_layers) 
    
    return {**remaining_arch_stats, **conv_stats}

In [25]:
def extract_conv_stats(conv_layers : list) -> dict:
    conv_statistics = {'conv_num_layers': 0, 'conv_kernel_min': 0, 'conv_kernel_max': 0, 'conv_kernel_mode': 0}

    if len(conv_layers) > 0:
        conv_statistics['conv_num_layers'] = len(conv_layers)
        conv_statistics['conv_kernel_min'] = min(conv_layers) 
        conv_statistics['conv_kernel_max'] = max(conv_layers) 
        conv_statistics['conv_kernel_mode'] = stats.mode(conv_layers)[0][0]
  
    return conv_statistics

In [26]:
api = API('/home/gean/datasets/NAS-Bench-201-v1_1-096897.pth')

try to create the NAS-Bench-201 api from /home/gean/datasets/NAS-Bench-201-v1_1-096897.pth


In [ ]:
# if __name__ == '__main__':
#     'setname': []
model_metafeatures = {'id_arch': [], 'str_arch': [], 'layers_all': [], 'adjacency_matrix': [], 'dataset': [], 'epoch': [], 
                          'conv_num_layers': [], 'conv_kernel_min': [], 'conv_kernel_max': [], 'conv_kernel_mode': [],
                          'avg_pool_num_layers': [], 'skip_connection_num_layers': [], 'zeroize_num_layers': [],
                          'flops': [], 'params': [], 'latency': [], 'time_train': [], 'time_valid': [], 'time_test': [], 
                          'loss_train': [], 'loss_valid': [], 'loss_test': [], 'acc_train': [], 'acc_valid': [], 'acc_test': []}

    # datasets: cifar10-valid : training the model on the CIFAR-10 training set.
    #           cifar10 : training the model on the CIFAR-10 training + validation set.
    #           cifar100 : training the model on the CIFAR-100 training set.
    #           ImageNet16-120 : training the model on the ImageNet16-120 training set.
            
    # setname: for cifar10-valid -> 'train' (metric on train set), 'x-valid' (metric on validation set), 'ori-test' (metric on test set)
    #          for cifar10 -> 'train' (metric on train + validation set), 'ori-test' (metric on test set)
    #          for cifar100 and ImageNet16-120 -> 'train' (metric on train set), 'x-valid' (metric on validation set), 
    #             'x-test' (metric on test set), 'ori-test' (metric on validation + test set)
datasets_setnames = {'cifar10-valid': ['train', 'x-valid', 'ori-test'], 
#                      'cifar10': ['train', 'ori-test', ], 
                     'cifar100': ['train', 'x-valid', 'x-test'], 
                     'ImageNet16-120': ['train', 'x-valid', 'x-test']}
    
epochs = [0, 3, 11, 35, 107, 199]
    
#iter over all 15k archs
for arch_idx, arch_str in enumerate(api):
    info = api.query_meta_info_by_index(arch_idx, hp='200')  #`ArchResults` instance
    print("\ninfo: {}".format(info))
        
    layers = extract_layers(api, arch_str)
    arch_stats = get_arch_stats(layers)
        
    for dataset in datasets_setnames.keys():
        print("\n######## {} ########".format(dataset))
        
        cost_metrics = info.get_compute_costs(dataset) 
#         print("\ncost_metrics: ", cost_metrics)
                
        for epoch in epochs:
            print("epoch {}".format(epoch+1))
            #unique from each arch
            model_metafeatures['id_arch'].append(arch_idx)
            model_metafeatures['str_arch'].append(arch_str)
            model_metafeatures['layers_all'].append(layers)
            model_metafeatures['adjacency_matrix'].append(api.str2matrix(arch_str))

            model_metafeatures['dataset'].append(dataset)
            #epoch=epoch-1, so 0 (min), {3, 11, 35, 107} (same as nasbench101), and 199 (max)
            model_metafeatures['epoch'].append(int(epoch)+1) 
                        
            #simple model-based statistical meta-features
            model_metafeatures['conv_num_layers'].append(arch_stats['conv_num_layers'])
            model_metafeatures['conv_kernel_min'].append(arch_stats['conv_kernel_min'])
            model_metafeatures['conv_kernel_max'].append(arch_stats['conv_kernel_max'])
            model_metafeatures['conv_kernel_mode'].append(arch_stats['conv_kernel_mode'])
            model_metafeatures['avg_pool_num_layers'].append(arch_stats['avg_pool_num_layers'])
            model_metafeatures['skip_connection_num_layers'].append(arch_stats['skip_connection_num_layers'])
            model_metafeatures['zeroize_num_layers'].append(arch_stats['zeroize_num_layers'])

            model_metafeatures['flops'].append(cost_metrics['flops'])
            model_metafeatures['params'].append(cost_metrics['params'])
            model_metafeatures['latency'].append(cost_metrics['latency'])
                
            for setname in datasets_setnames.get(dataset):
                aux = setname.split('-')
                    
                try:
                    res_metrics = info.get_metrics(dataset=dataset, setname=setname, iepoch=epoch, is_random=False) 
#                     print("{}: {}".format(setname, res_metrics))
                        
                    model_metafeatures[str('loss_' + aux[len(aux)-1])].append(res_metrics['loss'])
                    model_metafeatures[str('acc_' + aux[len(aux)-1])].append(res_metrics['accuracy'])
                    model_metafeatures[str('time_' + aux[len(aux)-1])].append(res_metrics['all_time']) #from first epoch until now
                        
                except KeyError as e:
#                     print("\ntype error: " + str(e), "\n") 
                    aux = setname.split('-')
                        
                    #since we have to generate keys with the same number of values
                    model_metafeatures[str('loss_' + aux[len(aux)-1])].append(None)
                    model_metafeatures[str('acc_' + aux[len(aux)-1])].append(None)
                    model_metafeatures[str('time_' + aux[len(aux)-1])].append(None)          
model_metafeatures

Call query_meta_info_by_index with arch_index=0, hp=200

info: ArchResults(arch-index=0, arch=|avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~1|+|nor_conv_1x1~0|skip_connect~1|skip_connect~2|, 12 runs, clear=True)

######## cifar10-valid ########
epoch 1
epoch 4
epoch 12
epoch 36
epoch 108
epoch 200

######## cifar100 ########
epoch 1
epoch 4
epoch 12
epoch 36
epoch 108
epoch 200

######## ImageNet16-120 ########
epoch 1
epoch 4
epoch 12
epoch 36
epoch 108
epoch 200
Call query_meta_info_by_index with arch_index=1, hp=200

info: ArchResults(arch-index=1, arch=|nor_conv_3x3~0|+|nor_conv_3x3~0|avg_pool_3x3~1|+|skip_connect~0|nor_conv_3x3~1|skip_connect~2|, 12 runs, clear=True)

######## cifar10-valid ########
epoch 1
epoch 4
epoch 12
epoch 36
epoch 108
epoch 200

######## cifar100 ########
epoch 1
epoch 4
epoch 12
epoch 36
epoch 108
epoch 200

######## ImageNet16-120 ########
epoch 1
epoch 4
epoch 12
epoch 36
epoch 108
epoch 200
Call query_meta_info_by_index with arch_index=2, hp=200

info:

In [29]:
df = pd.DataFrame.from_dict(model_metafeatures, orient='index').transpose()
df

id_arch                                           str_arch  \
0            0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
1            0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
2            0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
3            0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
4            0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
...        ...                                                ...   
281245   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   
281246   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   
281247   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   
281248   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   
281249   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   

                                               layers_all  \
0       [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
1       [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
2       [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
3       [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
4       [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
...                                                   ...   
281245  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   
281246  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   
281247  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   
281248  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   
281249  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   

                                         adjacency_matrix         dataset  \
0       [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...   cifar10-valid   
1       [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...   cifar10-valid   
2       [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...   cifar10-valid   
3       [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...   cifar10-valid   
4       [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...   cifar10-valid   
...                                                   ...             ...   
281245  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   
281246  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   
281247  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   
281248  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   
281249  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   

       epoch conv_num_layers conv_kernel_min conv_kernel_max conv_kernel_mode  \
0          1               2               1               1                1   
1          4               2               1               1                1   
2         12               2               1               1                1   
3         36               2               1               1                1   
4        108               2               1               1                1   
...      ...             ...             ...             ...              ...   
281245     4               4               1               1                1   
281246    12               4               1               1                1   
281247    36               4               1               1                1   
281248   108               4               1               1                1   
281249   200               4               1               1                1   

        ...   latency    time_train  time_valid  time_test loss_train  \
0       ...  0.013936      7.221093    2.548979       None   1.919065   
1       ...  0.013936     28.884372   10.195917       None   1.504583   
2       ...  0.013936     86.653116   30.587751       None   1.166258   
3       ...  0.013936    259.959348   91.763253       None    0.91874   
4       ...  0.013936    779.878044  275.289758       None   0.672449   
...     ...       ...           ...         ...        ...        ...   
281245  ...  0.020879     253.56949 

In [38]:
df.to_csv('/home/gean/nns_performance_prediction/meta_datasets/nasbench201_tabular.csv', float_format='%.6f')

In [39]:
df_cifar10valid = df.loc[(df['dataset'] == 'cifar10-valid')]
df_cifar10valid.to_csv('/home/gean/nns_performance_prediction/meta_datasets/nasbench201_cifar10valid.csv', float_format='%.6f')
df_cifar10valid

id_arch                                           str_arch  \
0            0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
1            0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
2            0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
3            0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
4            0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
...        ...                                                ...   
281233   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   
281234   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   
281235   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   
281236   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   
281237   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   

                                               layers_all  \
0       [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
1       [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
2       [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
3       [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
4       [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
...                                                   ...   
281233  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   
281234  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   
281235  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   
281236  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   
281237  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   

                                         adjacency_matrix        dataset  \
0       [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
1       [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
2       [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
3       [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
4       [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
...                                                   ...            ...   
281233  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281234  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281235  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281236  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281237  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  cifar10-valid   

       epoch conv_num_layers conv_kernel_min conv_kernel_max conv_kernel_mode  \
0          1               2               1               1                1   
1          4               2               1               1                1   
2         12               2               1               1                1   
3         36               2               1               1                1   
4        108               2               1               1                1   
...      ...             ...             ...             ...              ...   
281233     4               4               1               1                1   
281234    12               4               1               1                1   
281235    36               4               1               1                1   
281236   108               4               1               1                1   
281237   200               4               1               1                1   

        ...   latency   time_train  time_valid   time_test loss_train  \
0       ...  0.013936     7.221093    2.548979        None   1.919065   
1       ...  0.013936    28.884372   10.195917        None   1.504583   
2       ...  0.013936    86.653116   30.587751        None   1.166258   
3       ...  0.013936   259.959348   91.763253        None    0.91874   
4       ...  0.013936   779.878044  275.289758        None   0.672449   
...     ...       ...          ...         ...         ...        ...   
281233  ...  0.019546    41.787984   12.722857  

In [40]:
df_cifar100 = df.loc[(df['dataset'] == 'cifar100')]
df_cifar100.to_csv('/home/gean/nns_performance_prediction/meta_datasets/nasbench201_cifar100.csv', float_format='%.6f')
df_cifar100

id_arch                                           str_arch  \
6            0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
7            0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
8            0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
9            0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
10           0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
...        ...                                                ...   
281239   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   
281240   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   
281241   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   
281242   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   
281243   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   

                                               layers_all  \
6       [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
7       [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
8       [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
9       [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
10      [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
...                                                   ...   
281239  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   
281240  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   
281241  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   
281242  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   
281243  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   

                                         adjacency_matrix   dataset epoch  \
6       [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar100     1   
7       [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar100     4   
8       [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar100    12   
9       [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar100    36   
10      [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar100   108   
...                                                   ...       ...   ...   
281239  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  cifar100     4   
281240  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  cifar100    12   
281241  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  cifar100    36   
281242  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  cifar100   108   
281243  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  cifar100   200   

       conv_num_layers conv_kernel_min conv_kernel_max conv_kernel_mode  ...  \
6                    2               1               1                1  ...   
7                    2               1               1                1  ...   
8                    2               1               1                1  ...   
9                    2               1               1                1  ...   
10                   2               1               1                1  ...   
...                ...             ...             ...              ...  ...   
281239               4               1               1                1  ...   
281240               4               1               1                1  ...   
281241               4               1               1                1  ...   
281242               4               1               1                1  ...   
281243               4               1               1                1  ...   

         latency   time_train  time_valid   time_test loss_train loss_valid  \
6       0.013183    14.442186        None        None    4.17827       None   
7       0.013183    57.768744        None        None   3.445706       None   
8       0.013183   173.306232        None        None   2.862544       None   
9       0.013183   519.918696        None        None   2.466167       None   
10      0.013183  1559.756088        None        None   2.076255       None   
...          ...          ...         ...         ...        ...        ...   
281239

In [42]:
df_imagenet16_120 = df.loc[(df['dataset'] == 'ImageNet16-120')]
df_imagenet16_120.to_csv('/home/gean/nns_performance_prediction/meta_datasets/nasbench201_imagenet16_120.csv', float_format='%.6f')
df_imagenet16_120

id_arch                                           str_arch  \
12           0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
13           0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
14           0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
15           0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
16           0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
...        ...                                                ...   
281245   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   
281246   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   
281247   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   
281248   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   
281249   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   

                                               layers_all  \
12      [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
13      [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
14      [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
15      [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
16      [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
...                                                   ...   
281245  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   
281246  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   
281247  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   
281248  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   
281249  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   

                                         adjacency_matrix         dataset  \
12      [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   
13      [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   
14      [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   
15      [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   
16      [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   
...                                                   ...             ...   
281245  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   
281246  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   
281247  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   
281248  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   
281249  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   

       epoch conv_num_layers conv_kernel_min conv_kernel_max conv_kernel_mode  \
12         1               2               1               1                1   
13         4               2               1               1                1   
14        12               2               1               1                1   
15        36               2               1               1                1   
16       108               2               1               1                1   
...      ...             ...             ...             ...              ...   
281245     4               4               1               1                1   
281246    12               4               1               1                1   
281247    36               4               1               1                1   
281248   108               4               1               1                1   
281249   200               4               1               1                1   

        ...   latency    time_train time_valid  time_test loss_train  \
12      ...  0.012977     43.817592       None       None   4.460797   
13      ...  0.012977    175.270369       None       None   3.941375   
14      ...  0.012977    525.811108       None       None   3.753587   
15      ...  0.012977   1577.433323       None       None   3.616714   
16      ...  0.012977    4732.29997       None       None   3.408893   
...     ...       ...           ...        ...        ...        ...   
281245  ...  0.020879     253.56949       N

In [44]:
df_cifar10valid_4epochs = df.loc[(df['dataset'] == 'cifar10-valid') & (df['epoch'] == 4)]
df_cifar10valid_4epochs.to_csv('/home/gean/nns_performance_prediction/meta_datasets/nasbench201_cifar10valid_4epochs.csv',
                               float_format='%.6f')
df_cifar10valid_4epochs

id_arch                                           str_arch  \
1            0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
19           1  |nor_conv_3x3~0|+|nor_conv_3x3~0|avg_pool_3x3~...   
37           2  |avg_pool_3x3~0|+|nor_conv_3x3~0|nor_conv_3x3~...   
55           3  |avg_pool_3x3~0|+|skip_connect~0|none~1|+|none...   
73           4  |skip_connect~0|+|skip_connect~0|nor_conv_1x1~...   
...        ...                                                ...   
281161   15620  |none~0|+|avg_pool_3x3~0|avg_pool_3x3~1|+|skip...   
281179   15621  |avg_pool_3x3~0|+|nor_conv_3x3~0|nor_conv_3x3~...   
281197   15622  |skip_connect~0|+|nor_conv_3x3~0|nor_conv_3x3~...   
281215   15623  |none~0|+|avg_pool_3x3~0|avg_pool_3x3~1|+|avg_...   
281233   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   

                                               layers_all  \
1       [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
19      [nor_conv_3x3, nor_conv_3x3, avg_pool_3x3, ski...   
37      [avg_pool_3x3, nor_conv_3x3, nor_conv_3x3, avg...   
55      [avg_pool_3x3, skip_connect, none, none, none,...   
73      [skip_connect, skip_connect, nor_conv_1x1, ski...   
...                                                   ...   
281161  [none, avg_pool_3x3, avg_pool_3x3, skip_connec...   
281179  [avg_pool_3x3, nor_conv_3x3, nor_conv_3x3, ski...   
281197  [skip_connect, nor_conv_3x3, nor_conv_3x3, nor...   
281215  [none, avg_pool_3x3, avg_pool_3x3, avg_pool_3x...   
281233  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   

                                         adjacency_matrix        dataset  \
1       [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
19      [[0.0, 0.0, 0.0, 0.0], [3.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
37      [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
55      [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
73      [[0.0, 0.0, 0.0, 0.0], [1.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
...                                                   ...            ...   
281161  [[0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281179  [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281197  [[0.0, 0.0, 0.0, 0.0], [1.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281215  [[0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281233  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  cifar10-valid   

       epoch conv_num_layers conv_kernel_min conv_kernel_max conv_kernel_mode  \
1          4               2               1               1                1   
19         4               3               3               3                3   
37         4               2               3               3                3   
55         4               0               0               0                0   
73         4               2               1               1                1   
...      ...             ...             ...             ...              ...   
281161     4               0               0               0                0   
281179     4               3               1               3                3   
281197     4               4               1               3                3   
281215     4               0               0               0                0   
281233     4               4               1               1                1   

        ...   latency time_train time_valid time_test loss_train loss_valid  \
1       ...  0.013936  28.884372  10.195917      None   1.504583   1.919403   
19      ...  0.016853  43.392828  15.016796      None   0.943213   1.348791   
37      ...  0.014428  45.343554  15.896988      None   1.445244   1.637992   
55      ...  0.009291   16.66098   9.746239      None   1.123983     1.3992   
73      ...  0.013826  25.937196   9.652641      None   1.532887    1.69192   
...     ...       ...        ...        ...       ...        ...        ...   
281161

In [45]:
df_cifar10valid_12epochs = df.loc[(df['dataset'] == 'cifar10-valid') & (df['epoch'] == 12)]
df_cifar10valid_12epochs.to_csv('/home/gean/nns_performance_prediction/meta_datasets/nasbench201_cifar10valid_12epochs.csv',
                               float_format='%.6f')
df_cifar10valid_12epochs

id_arch                                           str_arch  \
2            0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
20           1  |nor_conv_3x3~0|+|nor_conv_3x3~0|avg_pool_3x3~...   
38           2  |avg_pool_3x3~0|+|nor_conv_3x3~0|nor_conv_3x3~...   
56           3  |avg_pool_3x3~0|+|skip_connect~0|none~1|+|none...   
74           4  |skip_connect~0|+|skip_connect~0|nor_conv_1x1~...   
...        ...                                                ...   
281162   15620  |none~0|+|avg_pool_3x3~0|avg_pool_3x3~1|+|skip...   
281180   15621  |avg_pool_3x3~0|+|nor_conv_3x3~0|nor_conv_3x3~...   
281198   15622  |skip_connect~0|+|nor_conv_3x3~0|nor_conv_3x3~...   
281216   15623  |none~0|+|avg_pool_3x3~0|avg_pool_3x3~1|+|avg_...   
281234   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   

                                               layers_all  \
2       [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
20      [nor_conv_3x3, nor_conv_3x3, avg_pool_3x3, ski...   
38      [avg_pool_3x3, nor_conv_3x3, nor_conv_3x3, avg...   
56      [avg_pool_3x3, skip_connect, none, none, none,...   
74      [skip_connect, skip_connect, nor_conv_1x1, ski...   
...                                                   ...   
281162  [none, avg_pool_3x3, avg_pool_3x3, skip_connec...   
281180  [avg_pool_3x3, nor_conv_3x3, nor_conv_3x3, ski...   
281198  [skip_connect, nor_conv_3x3, nor_conv_3x3, nor...   
281216  [none, avg_pool_3x3, avg_pool_3x3, avg_pool_3x...   
281234  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   

                                         adjacency_matrix        dataset  \
2       [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
20      [[0.0, 0.0, 0.0, 0.0], [3.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
38      [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
56      [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
74      [[0.0, 0.0, 0.0, 0.0], [1.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
...                                                   ...            ...   
281162  [[0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281180  [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281198  [[0.0, 0.0, 0.0, 0.0], [1.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281216  [[0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281234  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  cifar10-valid   

       epoch conv_num_layers conv_kernel_min conv_kernel_max conv_kernel_mode  \
2         12               2               1               1                1   
20        12               3               3               3                3   
38        12               2               3               3                3   
56        12               0               0               0                0   
74        12               2               1               1                1   
...      ...             ...             ...             ...              ...   
281162    12               0               0               0                0   
281180    12               3               1               3                3   
281198    12               4               1               3                3   
281216    12               0               0               0                0   
281234    12               4               1               1                1   

        ...   latency  time_train time_valid time_test loss_train loss_valid  \
2       ...  0.013936   86.653116  30.587751      None   1.166258   1.733641   
20      ...  0.016853  130.178483  45.050388      None   0.517074   0.904066   
38      ...  0.014428  136.030661  47.690964      None   1.122346   1.433284   
56      ...  0.009291   49.982939  29.238718      None   0.795997   1.042909   
74      ...  0.013826   77.811589  28.957922      None   1.126775   2.333692   
...     ...       ...         ...        ...       ...        ...        ...   

In [46]:
df_cifar10valid_36epochs = df.loc[(df['dataset'] == 'cifar10-valid') & (df['epoch'] == 36)]
df_cifar10valid_36epochs.to_csv('/home/gean/nns_performance_prediction/meta_datasets/nasbench201_cifar10valid_36epochs.csv',
                               float_format='%.6f')
df_cifar10valid_36epochs

id_arch                                           str_arch  \
3            0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
21           1  |nor_conv_3x3~0|+|nor_conv_3x3~0|avg_pool_3x3~...   
39           2  |avg_pool_3x3~0|+|nor_conv_3x3~0|nor_conv_3x3~...   
57           3  |avg_pool_3x3~0|+|skip_connect~0|none~1|+|none...   
75           4  |skip_connect~0|+|skip_connect~0|nor_conv_1x1~...   
...        ...                                                ...   
281163   15620  |none~0|+|avg_pool_3x3~0|avg_pool_3x3~1|+|skip...   
281181   15621  |avg_pool_3x3~0|+|nor_conv_3x3~0|nor_conv_3x3~...   
281199   15622  |skip_connect~0|+|nor_conv_3x3~0|nor_conv_3x3~...   
281217   15623  |none~0|+|avg_pool_3x3~0|avg_pool_3x3~1|+|avg_...   
281235   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   

                                               layers_all  \
3       [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
21      [nor_conv_3x3, nor_conv_3x3, avg_pool_3x3, ski...   
39      [avg_pool_3x3, nor_conv_3x3, nor_conv_3x3, avg...   
57      [avg_pool_3x3, skip_connect, none, none, none,...   
75      [skip_connect, skip_connect, nor_conv_1x1, ski...   
...                                                   ...   
281163  [none, avg_pool_3x3, avg_pool_3x3, skip_connec...   
281181  [avg_pool_3x3, nor_conv_3x3, nor_conv_3x3, ski...   
281199  [skip_connect, nor_conv_3x3, nor_conv_3x3, nor...   
281217  [none, avg_pool_3x3, avg_pool_3x3, avg_pool_3x...   
281235  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   

                                         adjacency_matrix        dataset  \
3       [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
21      [[0.0, 0.0, 0.0, 0.0], [3.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
39      [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
57      [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
75      [[0.0, 0.0, 0.0, 0.0], [1.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
...                                                   ...            ...   
281163  [[0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281181  [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281199  [[0.0, 0.0, 0.0, 0.0], [1.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281217  [[0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281235  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  cifar10-valid   

       epoch conv_num_layers conv_kernel_min conv_kernel_max conv_kernel_mode  \
3         36               2               1               1                1   
21        36               3               3               3                3   
39        36               2               3               3                3   
57        36               0               0               0                0   
75        36               2               1               1                1   
...      ...             ...             ...             ...              ...   
281163    36               0               0               0                0   
281181    36               3               1               3                3   
281199    36               4               1               3                3   
281217    36               0               0               0                0   
281235    36               4               1               1                1   

        ...   latency  time_train  time_valid time_test loss_train loss_valid  \
3       ...  0.013936  259.959348   91.763253      None    0.91874   1.617924   
21      ...  0.016853  390.535448  135.151163      None   0.304653    0.60907   
39      ...  0.014428  408.091982  143.072891      None   0.906255   1.267598   
57      ...  0.009291  149.948818   87.716155      None   0.585472   0.861307   
75      ...  0.013826  233.434766   86.873766      None   0.878979   1.272511   
...     ...       ...         ...         ...       ...        ...       

In [47]:
df_cifar10valid_108epochs = df.loc[(df['dataset'] == 'cifar10-valid') & (df['epoch'] == 108)]
df_cifar10valid_108epochs.to_csv('/home/gean/nns_performance_prediction/meta_datasets/nasbench201_cifar10valid_108epochs.csv',
                               float_format='%.6f')
df_cifar10valid_108epochs

id_arch                                           str_arch  \
4            0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
22           1  |nor_conv_3x3~0|+|nor_conv_3x3~0|avg_pool_3x3~...   
40           2  |avg_pool_3x3~0|+|nor_conv_3x3~0|nor_conv_3x3~...   
58           3  |avg_pool_3x3~0|+|skip_connect~0|none~1|+|none...   
76           4  |skip_connect~0|+|skip_connect~0|nor_conv_1x1~...   
...        ...                                                ...   
281164   15620  |none~0|+|avg_pool_3x3~0|avg_pool_3x3~1|+|skip...   
281182   15621  |avg_pool_3x3~0|+|nor_conv_3x3~0|nor_conv_3x3~...   
281200   15622  |skip_connect~0|+|nor_conv_3x3~0|nor_conv_3x3~...   
281218   15623  |none~0|+|avg_pool_3x3~0|avg_pool_3x3~1|+|avg_...   
281236   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   

                                               layers_all  \
4       [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
22      [nor_conv_3x3, nor_conv_3x3, avg_pool_3x3, ski...   
40      [avg_pool_3x3, nor_conv_3x3, nor_conv_3x3, avg...   
58      [avg_pool_3x3, skip_connect, none, none, none,...   
76      [skip_connect, skip_connect, nor_conv_1x1, ski...   
...                                                   ...   
281164  [none, avg_pool_3x3, avg_pool_3x3, skip_connec...   
281182  [avg_pool_3x3, nor_conv_3x3, nor_conv_3x3, ski...   
281200  [skip_connect, nor_conv_3x3, nor_conv_3x3, nor...   
281218  [none, avg_pool_3x3, avg_pool_3x3, avg_pool_3x...   
281236  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   

                                         adjacency_matrix        dataset  \
4       [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
22      [[0.0, 0.0, 0.0, 0.0], [3.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
40      [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
58      [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
76      [[0.0, 0.0, 0.0, 0.0], [1.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
...                                                   ...            ...   
281164  [[0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281182  [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281200  [[0.0, 0.0, 0.0, 0.0], [1.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281218  [[0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281236  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  cifar10-valid   

       epoch conv_num_layers conv_kernel_min conv_kernel_max conv_kernel_mode  \
4        108               2               1               1                1   
22       108               3               3               3                3   
40       108               2               3               3                3   
58       108               0               0               0                0   
76       108               2               1               1                1   
...      ...             ...             ...             ...              ...   
281164   108               0               0               0                0   
281182   108               3               1               3                3   
281200   108               4               1               3                3   
281218   108               0               0               0                0   
281236   108               4               1               1                1   

        ...   latency   time_train  time_valid time_test loss_train  \
4       ...  0.013936   779.878044  275.289758      None   0.672449   
22      ...  0.016853  1171.606343   405.45349      None    0.10793   
40      ...  0.014428  1224.275946  429.218674      None   0.654087   
58      ...  0.009291   449.846453  263.148464      None    0.43916   
76      ...  0.013826   700.304299  260.621299      None    0.60091   
...     ...       ...          ...         ...       ...        ...   
281164  ...  0.009765   544.096637  259.217422      None   0.4

In [49]:
df_cifar10valid_200epochs = df.loc[(df['dataset'] == 'cifar10-valid') & (df['epoch'] == 200)]
df_cifar10valid_200epochs.to_csv('/home/gean/nns_performance_prediction/meta_datasets/nasbench201_cifar10valid_200epochs.csv',
                               float_format='%.6f')
df_cifar10valid_200epochs

id_arch                                           str_arch  \
5            0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
23           1  |nor_conv_3x3~0|+|nor_conv_3x3~0|avg_pool_3x3~...   
41           2  |avg_pool_3x3~0|+|nor_conv_3x3~0|nor_conv_3x3~...   
59           3  |avg_pool_3x3~0|+|skip_connect~0|none~1|+|none...   
77           4  |skip_connect~0|+|skip_connect~0|nor_conv_1x1~...   
...        ...                                                ...   
281165   15620  |none~0|+|avg_pool_3x3~0|avg_pool_3x3~1|+|skip...   
281183   15621  |avg_pool_3x3~0|+|nor_conv_3x3~0|nor_conv_3x3~...   
281201   15622  |skip_connect~0|+|nor_conv_3x3~0|nor_conv_3x3~...   
281219   15623  |none~0|+|avg_pool_3x3~0|avg_pool_3x3~1|+|avg_...   
281237   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   

                                               layers_all  \
5       [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
23      [nor_conv_3x3, nor_conv_3x3, avg_pool_3x3, ski...   
41      [avg_pool_3x3, nor_conv_3x3, nor_conv_3x3, avg...   
59      [avg_pool_3x3, skip_connect, none, none, none,...   
77      [skip_connect, skip_connect, nor_conv_1x1, ski...   
...                                                   ...   
281165  [none, avg_pool_3x3, avg_pool_3x3, skip_connec...   
281183  [avg_pool_3x3, nor_conv_3x3, nor_conv_3x3, ski...   
281201  [skip_connect, nor_conv_3x3, nor_conv_3x3, nor...   
281219  [none, avg_pool_3x3, avg_pool_3x3, avg_pool_3x...   
281237  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   

                                         adjacency_matrix        dataset  \
5       [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
23      [[0.0, 0.0, 0.0, 0.0], [3.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
41      [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
59      [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
77      [[0.0, 0.0, 0.0, 0.0], [1.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
...                                                   ...            ...   
281165  [[0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281183  [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281201  [[0.0, 0.0, 0.0, 0.0], [1.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281219  [[0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0], [...  cifar10-valid   
281237  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  cifar10-valid   

       epoch conv_num_layers conv_kernel_min conv_kernel_max conv_kernel_mode  \
5        200               2               1               1                1   
23       200               3               3               3                3   
41       200               2               3               3                3   
59       200               0               0               0                0   
77       200               2               1               1                1   
...      ...             ...             ...             ...              ...   
281165   200               0               0               0                0   
281183   200               3               1               3                3   
281201   200               4               1               3                3   
281219   200               0               0               0                0   
281237   200               4               1               1                1   

        ...   latency   time_train  time_valid   time_test loss_train  \
5       ...  0.013936    1444.2186  509.795847  203.918339   0.319028   
23      ...  0.016853  2169.641376  750.839795  300.335918   0.001767   
41      ...  0.014428  2267.177677  794.849396  317.939758   0.308339   
59      ...  0.009291   833.048987  487.311971  194.924788   0.262831   
77      ...  0.013826  1296.859813  482.632035  193.052814   0.255936   
...     ...       ...          ...         ...         ...        ...   
281165  ...  0.009765  1007.586364  480.032262  

In [50]:
df_cifar100_200epochs = df.loc[(df['dataset'] == 'cifar100') & (df['epoch'] == 200)]
df_cifar100_200epochs.to_csv('/home/gean/nns_performance_prediction/meta_datasets/nasbench201_cifar100_200epochs.csv',
                               float_format='%.6f')
df_cifar100_200epochs

id_arch                                           str_arch  \
11           0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
29           1  |nor_conv_3x3~0|+|nor_conv_3x3~0|avg_pool_3x3~...   
47           2  |avg_pool_3x3~0|+|nor_conv_3x3~0|nor_conv_3x3~...   
65           3  |avg_pool_3x3~0|+|skip_connect~0|none~1|+|none...   
83           4  |skip_connect~0|+|skip_connect~0|nor_conv_1x1~...   
...        ...                                                ...   
281171   15620  |none~0|+|avg_pool_3x3~0|avg_pool_3x3~1|+|skip...   
281189   15621  |avg_pool_3x3~0|+|nor_conv_3x3~0|nor_conv_3x3~...   
281207   15622  |skip_connect~0|+|nor_conv_3x3~0|nor_conv_3x3~...   
281225   15623  |none~0|+|avg_pool_3x3~0|avg_pool_3x3~1|+|avg_...   
281243   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   

                                               layers_all  \
11      [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
29      [nor_conv_3x3, nor_conv_3x3, avg_pool_3x3, ski...   
47      [avg_pool_3x3, nor_conv_3x3, nor_conv_3x3, avg...   
65      [avg_pool_3x3, skip_connect, none, none, none,...   
83      [skip_connect, skip_connect, nor_conv_1x1, ski...   
...                                                   ...   
281171  [none, avg_pool_3x3, avg_pool_3x3, skip_connec...   
281189  [avg_pool_3x3, nor_conv_3x3, nor_conv_3x3, ski...   
281207  [skip_connect, nor_conv_3x3, nor_conv_3x3, nor...   
281225  [none, avg_pool_3x3, avg_pool_3x3, avg_pool_3x...   
281243  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   

                                         adjacency_matrix   dataset epoch  \
11      [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar100   200   
29      [[0.0, 0.0, 0.0, 0.0], [3.0, 0.0, 0.0, 0.0], [...  cifar100   200   
47      [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar100   200   
65      [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar100   200   
83      [[0.0, 0.0, 0.0, 0.0], [1.0, 0.0, 0.0, 0.0], [...  cifar100   200   
...                                                   ...       ...   ...   
281171  [[0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0], [...  cifar100   200   
281189  [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  cifar100   200   
281207  [[0.0, 0.0, 0.0, 0.0], [1.0, 0.0, 0.0, 0.0], [...  cifar100   200   
281225  [[0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0], [...  cifar100   200   
281243  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  cifar100   200   

       conv_num_layers conv_kernel_min conv_kernel_max conv_kernel_mode  ...  \
11                   2               1               1                1  ...   
29                   3               3               3                3  ...   
47                   2               3               3                3  ...   
65                   0               0               0                0  ...   
83                   2               1               1                1  ...   
...                ...             ...             ...              ...  ...   
281171               0               0               0                0  ...   
281189               3               1               3                3  ...   
281207               4               1               3                3  ...   
281225               0               0               0                0  ...   
281243               4               1               1                1  ...   

         latency   time_train  time_valid   time_test loss_train loss_valid  \
11      0.013183    2888.4372  101.959169  101.959169   1.510741   1.741787   
29      0.015363  4339.282751  150.167959  150.167959   0.048054   1.373184   
47      0.014029  4534.355354  158.969879  158.969879   1.431623   1.701853   
65      0.009306  1666.097975   97.462394   97.462394   1.338988   1.539061   
83      0.012342  2593.719625   96.526407   96.526407   1.204578    1.43442   
...          ...          ...         ...         ...        ...        ...   
281171

In [51]:
df_imagenet16_120_200epochs = df.loc[(df['dataset'] == 'ImageNet16-120') & (df['epoch'] == 200)]
df_imagenet16_120_200epochs.to_csv('/home/gean/nns_performance_prediction/meta_datasets/nasbench201_imagenet16_120_200epochs.csv',
                               float_format='%.6f')
df_imagenet16_120_200epochs

id_arch                                           str_arch  \
17           0  |avg_pool_3x3~0|+|nor_conv_1x1~0|skip_connect~...   
35           1  |nor_conv_3x3~0|+|nor_conv_3x3~0|avg_pool_3x3~...   
53           2  |avg_pool_3x3~0|+|nor_conv_3x3~0|nor_conv_3x3~...   
71           3  |avg_pool_3x3~0|+|skip_connect~0|none~1|+|none...   
89           4  |skip_connect~0|+|skip_connect~0|nor_conv_1x1~...   
...        ...                                                ...   
281177   15620  |none~0|+|avg_pool_3x3~0|avg_pool_3x3~1|+|skip...   
281195   15621  |avg_pool_3x3~0|+|nor_conv_3x3~0|nor_conv_3x3~...   
281213   15622  |skip_connect~0|+|nor_conv_3x3~0|nor_conv_3x3~...   
281231   15623  |none~0|+|avg_pool_3x3~0|avg_pool_3x3~1|+|avg_...   
281249   15624  |nor_conv_1x1~0|+|none~0|nor_conv_1x1~1|+|none...   

                                               layers_all  \
17      [avg_pool_3x3, nor_conv_1x1, skip_connect, nor...   
35      [nor_conv_3x3, nor_conv_3x3, avg_pool_3x3, ski...   
53      [avg_pool_3x3, nor_conv_3x3, nor_conv_3x3, avg...   
71      [avg_pool_3x3, skip_connect, none, none, none,...   
89      [skip_connect, skip_connect, nor_conv_1x1, ski...   
...                                                   ...   
281177  [none, avg_pool_3x3, avg_pool_3x3, skip_connec...   
281195  [avg_pool_3x3, nor_conv_3x3, nor_conv_3x3, ski...   
281213  [skip_connect, nor_conv_3x3, nor_conv_3x3, nor...   
281231  [none, avg_pool_3x3, avg_pool_3x3, avg_pool_3x...   
281249  [nor_conv_1x1, none, nor_conv_1x1, none, nor_c...   

                                         adjacency_matrix         dataset  \
17      [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   
35      [[0.0, 0.0, 0.0, 0.0], [3.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   
53      [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   
71      [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   
89      [[0.0, 0.0, 0.0, 0.0], [1.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   
...                                                   ...             ...   
281177  [[0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   
281195  [[0.0, 0.0, 0.0, 0.0], [4.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   
281213  [[0.0, 0.0, 0.0, 0.0], [1.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   
281231  [[0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   
281249  [[0.0, 0.0, 0.0, 0.0], [2.0, 0.0, 0.0, 0.0], [...  ImageNet16-120   

       epoch conv_num_layers conv_kernel_min conv_kernel_max conv_kernel_mode  \
17       200               2               1               1                1   
35       200               3               3               3                3   
53       200               2               3               3                3   
71       200               0               0               0                0   
89       200               2               1               1                1   
...      ...             ...             ...             ...              ...   
281177   200               0               0               0                0   
281195   200               3               1               3                3   
281213   200               4               1               3                3   
281231   200               0               0               0                0   
281249   200               4               1               1                1   

        ...   latency    time_train time_valid  time_test loss_train  \
17      ...  0.012977   8763.518464  61.175502  61.175502   2.925081   
35      ...  0.013774  13165.383867  90.100775  90.100775   1.459219   
53      ...  0.012761  13757.234145  95.381927  95.381927   2.973894   
71      ...  0.008155   5054.941255  58.477436  58.477436   2.928704   
89      ...  0.011799   7869.345344  57.915844  57.915844   2.732304   
...     ...       ...           ...        ...        ...        ...   
281177  ...  0.009384   6114.034056  57.603